In [5]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML
from scipy import integrate

%matplotlib notebook



In [7]:
#Quaternion Playbox 

class Quaternion(np.ndarray):

#creates the Quaternion class and defines some useful methods

    def __new__(cls, Re, Im):
        '''
        Re is an integer. 
        Im is a list or an array.
        '''
        obj = np.concat([np.array([Re]), np.array(Im)]).view(cls)
        return obj
    
    def __array_finalize__(self, obj):
        return super().__array_finalize__(obj)

    
    def __mul__(Q1, Q2):
        Re = Q1[0]*Q2[0] - np.dot(Q1[1:4], Q2[1:4])
        Im = Q1[0] * Q2[1:4] + Q2[0] * Q1[1:4] + np.cross(Q1[1:4], Q2[1:4])
        return  Quaternion(Re, Im)
   
    def conjug(Q1):
        return Quaternion(Q1[0], -Q1[1:4])
    
    def rotate(v, q, theta):
        #v is a vector, q is the axis of rotation, theta the amount to rotate by
        V = Quaternion(0, v)
        Q = Quaternion(np.cos(theta/2), np.sin(theta/2) * np.array(q))
        return (Q*V)*Quaternion.conjug(Q)
    
    def norm(Q1):
        return np.sqrt(np.dot(Q1, Q1))
    
    def inverse(Q1):
        return Quaternion.conjug(Q1)/(Quaternion.norm(Q1))**2



In [11]:
q1 = Quaternion(3, [1, -2, 1])
q2 = Quaternion(2, [-1, 2, 3])

#rotate i hat about the y-axis 180 degrees, should give -i hat

print(q1[1:4])



[ 1 -2  1]


In [4]:
#Simple Pendulum + Animation playbox

#numerically solve pendulum: theta** + g/l sin(theta) = 0
G = 9.81
L = 1
theta = np.pi/3
omega = 0
totalPlotTime = 20 # 10 seconds
numSteps = 200 # memory considerations
dt = totalPlotTime / numSteps

thetas = []

for i in range(numSteps):
    
    thetas.append(theta)
    alpha = -G/L * np.sin(theta)
    omega = omega + alpha * dt
    theta = theta + omega * dt
    
thetas = np.array(thetas)

fig2 = plt.figure()

x = L * np.sin(thetas)
y = -L * np.cos(thetas)


# Create figure and pendulum line
fig = plt.figure()
ax = fig.add_subplot()


ax.set_aspect('equal')
ax.set_xlim(-L - 0.2, L + 0.2)
ax.set_ylim(-L - 0.2, 0.2)
ax.set_title("Simple Pendulum Animation")

(line,) = ax.plot([0, x[0]], [0, y[0]], 'o-', lw=2, color='royalblue')  # string
(trail,) = ax.plot([], [], '-', lw=1, color='lightblue', alpha=0.6)  # the shadow line

trail_length = 10  # number of frames for visible trail

def update(i):
    line.set_data([0, x[i]], [0, y[i]])

    start = max(i - trail_length, 0)
    trail.set_data(x[start:i], y[start:i])

    return (line, trail)
# Create the animation
ani = animation.FuncAnimation(fig, update, frames=numSteps, repeat=True, interval=30)

HTML(ani.to_jshtml())






<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

1. Naive implementation seems to work fine here
2. Pendulum isn't smooth-- that requires more timesteps.
3. Quaternions are a pain. Thankfully most of their math has been figured by previous authors and only their implementation remains. Still helpful to understand quaternions as vector rotations vs quaternions as coordinate frame rotations. 
4. Animation sucks. 